In [1]:
!pip install bert-score
!pip install rouge

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 102.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 58.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 58.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 85.9 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstallin

In [2]:
from time import time
import numpy as np
import pandas as pd
from bert_score import score
from rouge import Rouge
import ast

In [3]:
# compute base evaluation
def calculate_metrics(true_keywords, predicted_keywords):
    true_set = set(true_keywords)
    predicted_set = set(predicted_keywords)

    # Precision: Fraction of retrieved keywords that are relevant
    precision = len(true_set & predicted_set) / len(predicted_set) if predicted_set else 0

    # Recall: Fraction of relevant keywords that are retrieved
    recall = len(true_set & predicted_set) / len(true_set) if true_set else 0

    # F1-Score: Harmonic mean of Precision and Recall
    f1_score = (2 * precision * recall) / (precision + recall) if (precision + recall) > 0 else 0

    return precision, recall, f1_score

In [4]:
def bert_evaluation(ground_truth_keywords, extracted_keywords_cosine):
    # compute BERTscore evaluation
    metrics = {}
    bert_precision_scores_cosine = []
    bert_recall_scores_cosine = []
    bert_f1_scores_cosine = []

    start = time()
    for true_keywords, predicted_keywords in zip(ground_truth_keywords, extracted_keywords_cosine):

        #necessary not to have a reference to the original list
        padded_ground_truth = true_keywords.copy()
        padded_predicted = predicted_keywords.copy()

        if len(true_keywords) > len(predicted_keywords):

        #reference and predictions need to have the same size.
        #Therefore, if the number of ground truth keywords is higher than the chosen number of extracted keywords (10 in our case),
        #pad the list of predicted keywords with the "most relevant" keyword (according to cosine similarity with the document).
        #Other methods were possible, such as padding it with empty strings, or padding it with random keywords
            for i in range(len(true_keywords) - len(predicted_keywords)):
                padded_predicted.append(predicted_keywords[0])

        elif len(true_keywords) < len(predicted_keywords):
            #simply keep the "top-N" extracted keywords, where N is the length of the number of ground truth keywords
            padded_predicted = padded_predicted[:len(true_keywords)]

            # print(f"true keywords: {len(true_keywords)}")
            # print(f"predicted keywords: {len(predicted_keywords)}")
            # print(f"padded true keywords: {len(padded_ground_truth)}")
            # print(f"padded predicted keywords: {len(padded_predicted)}")

            precision, recall, f1_score = score(padded_predicted, padded_ground_truth, lang = 'en', verbose=True)
            # score results are of type torch.FloatTensor with 10 elements
            bert_precision_scores_cosine.append(precision.mean().item())
            bert_recall_scores_cosine.append(recall.mean().item())
            bert_f1_scores_cosine.append(f1_score.mean().item())

    bert_avg_precision_cosine = np.average(bert_precision_scores_cosine)
    bert_avg_recall_cosine = np.average(bert_recall_scores_cosine)
    bert_avg_f1_score_cosine = np.average(bert_f1_scores_cosine)

    end=time()

    metrics["bert_avg_precision_cosine"]=bert_avg_precision_cosine
    metrics["bert_avg_recall_cosine"]=bert_avg_recall_cosine
    metrics["bert_avg_f1_score_cosine"]=bert_avg_f1_score_cosine
    metrics["bert_time"]=end-start

    return metrics

In [5]:
def rouge_evaluation(ground_truth_keywords, extracted_keywords_cosine):
    # compute ROUGE score evaluation
    metrics = {}
    rouge = Rouge()

    rouge1_precision_scores = []
    rouge1_recall_scores = []
    rouge1_f1_scores = []

    rouge2_precision_scores = []
    rouge2_recall_scores = []
    rouge2_f1_scores = []

    rougeL_precision_scores = []
    rougeL_recall_scores = []
    rougeL_f1_scores = []

    start = time()

    #ROUGE compares two pieces of text. So merge the keywords in a single piece of text
    #separate the keywords with a '\n' separator, so that ROUGE treats them as separated sentences
    for true_keywords, predicted_keywords in zip(ground_truth_keywords, extracted_keywords_cosine):
        scores = rouge.get_scores('\n'.join(true_keywords), '\n'.join(predicted_keywords), avg=True)

        rouge1_precision_scores.append(scores["rouge-1"]["f"])
        rouge1_recall_scores.append(scores["rouge-1"]["p"])
        rouge1_f1_scores.append(scores["rouge-1"]["r"])

        rouge2_precision_scores.append(scores["rouge-2"]["f"])
        rouge2_recall_scores.append(scores["rouge-2"]["p"])
        rouge2_f1_scores.append(scores["rouge-2"]["r"])

        rougeL_precision_scores.append(scores["rouge-l"]["f"])
        rougeL_recall_scores.append(scores["rouge-l"]["p"])
        rougeL_f1_scores.append(scores["rouge-l"]["r"])

    rouge1_avg_precision = np.average(rouge1_precision_scores)
    rouge1_avg_recall = np.average(rouge1_recall_scores)
    rouge1_avg_f1_score = np.average(rouge1_f1_scores)

    rouge2_avg_precision = np.average(rouge2_precision_scores)
    rouge2_avg_recall = np.average(rouge2_recall_scores)
    rouge2_avg_f1_score = np.average(rouge2_f1_scores)

    rougeL_avg_precision = np.average(rougeL_precision_scores)
    rougeL_avg_recall = np.average(rougeL_recall_scores)
    rougeL_avg_f1_score = np.average(rougeL_f1_scores)

    end = time()

    metrics["rouge1_avg_precision"]=rouge1_avg_precision
    metrics["rouge1_avg_recall"]=rouge1_avg_recall
    metrics["rouge1_avg_f1_score"]=rouge1_avg_f1_score
    metrics["rouge2_avg_precision"]=rouge2_avg_precision
    metrics["rouge2_avg_recall"]=rouge2_avg_recall
    metrics["rouge2_avg_f1_score"]=rouge2_avg_f1_score
    metrics["rougeL_avg_precision"]=rougeL_avg_precision
    metrics["rougeL_avg_recall"]=rougeL_avg_recall
    metrics["rougeL_avg_f1_score"]=rougeL_avg_f1_score
    metrics["rouge_time"]=end-start

    return metrics

In [6]:
from time import time
def evaluation_method(groundtruth, extracted):
    metrics = {}
    start = time()
    cosine_precision_scores = []
    cosine_recall_scores = []
    cosine_f1_scores = []

    for true_keywords, predicted_keywords in zip(groundtruth, extracted):
        precision, recall, f1_score = calculate_metrics(true_keywords, predicted_keywords)

        cosine_precision_scores.append(precision)
        cosine_recall_scores.append(recall)
        cosine_f1_scores.append(f1_score)

    cosine_avg_precision = np.average(cosine_precision_scores)
    cosine_avg_recall = np.average(cosine_recall_scores)
    cosine_avg_f1_score = np.average(cosine_f1_scores)

    end = time()
    metric_time=end-start



    metrics["cosine_avg_precision"]=cosine_avg_precision
    metrics["cosine_avg_recall"]=cosine_avg_recall
    metrics["cosine_avg_f1_score"]=cosine_avg_f1_score
    metrics["cosine_time"]=metric_time

    metrics["bert"] = bert_evaluation(groundtruth, extracted)
    metrics["rouge"] = rouge_evaluation(groundtruth, extracted)

    return metrics

In [7]:
import ast

def complete_evaluation(dataset_name):
    print(f"Evaluation for dataset {dataset_name}")

    #download extracted keywords processed with method one

    extracted_keywords_cosine_one_path=f"https://raw.githubusercontent.com/s319848/DNLP-project-2025/main/notebooks/Second-extension/extension2_extraction_{dataset_name}_method_one.csv"

    extracted_one = pd.read_csv(extracted_keywords_cosine_one_path, header=None)
    extracted_keywords_cosine_one = extracted_one.iloc[:, 0].apply(ast.literal_eval).tolist()
    print(f"\nFirst element of extracted_keywords_cosine_one:\n{extracted_keywords_cosine_one[0]}")

    # download extracted keywords processed with method two

    extracted_keywords_cosine_two_path=f"https://raw.githubusercontent.com/s319848/DNLP-project-2025/main/notebooks/Second-extension/extension2_extraction_{dataset_name}_method_two.csv"

    extracted_two = pd.read_csv(extracted_keywords_cosine_two_path, header=None)
    extracted_keywords_cosine_two = extracted_two.iloc[:, 0].apply(ast.literal_eval).tolist()
    print(f"\nFirst element of extracted_keywords_cosine_two:\n{extracted_keywords_cosine_two[0]}")

    # download ground truth keywords
    ground_truth_path=f"https://raw.githubusercontent.com/s319848/DNLP-project-2025/main/notebooks/Second-extension/extension2_groundtruth_{dataset_name}.csv"
    groundtruth = pd.read_csv(ground_truth_path, header=None)
    groundtruth_k = groundtruth.iloc[:, 0].apply(ast.literal_eval).tolist()
    groundtruth_keywords=[]
    for kws in groundtruth_k:
            # Convert to lowercase, strip spaces, and create a set to remove duplicates
            unique_kws = list(set(kw.lower().strip() for kw in kws))
            groundtruth_keywords.append(unique_kws)
    print(f"First element of groundtruth_keywords:\n{groundtruth_keywords[0]}")

    print(f"Evaluation of method one...")
    metrics_one = evaluation_method(groundtruth=groundtruth_keywords, extracted=extracted_keywords_cosine_one)
    print(f"\n------\nEvaluation of method two...")
    metrics_two = evaluation_method(groundtruth=groundtruth_keywords, extracted=extracted_keywords_cosine_two)

    return metrics_one,metrics_two

In [8]:
one_n,two_n = complete_evaluation("Nguyen2007")
one_s,two_s = complete_evaluation("Semeval2010")

Evaluation for dataset Nguyen2007

First element of extracted_keywords_cosine_one:
['entropy ramsey graphs', 'ramsey graphs entropy', 'polynomial entropy ramsey', 'ramsey bipartite graphs', 'bipartite ramsey graphs', 'entropy ramsey', 'ramsey graphs frankl', 'extractors entropy', '2n ramsey graphs', 'ramsey graphs']

First element of extracted_keywords_cosine_two:
['entropy ramsey graphs', 'ramsey graphs entropy', 'ramsey bipartite graphs', 'bipartite ramsey graphs', 'entropy ramsey', 'ramsey graphs frankl', 'extractors entropy note', 'extractors entropy', 'source extractors entropy', 'ordinary ramsey graphs']
First element of groundtruth_keywords:
['independent source', 'block-sources', 'sum-product theorem', 'randomness extraction', 'distribution', 'dispersers', 'ramsey graphs', 'algorithms', 'ramsey graph', 'polynomial time computable disperser', 'tools', 'construction of disperser', 'bipartite graph', 'resiliency', 'extractors', 'subsource somewhere extractorramsey graphs', 'struct

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/482 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

...

calculating scores...
computing bert embedding.


  0%|          | 0/1 [00:00<?, ?it/s]

computing greedy matching.


  0%|          | 0/1 [00:00<?, ?it/s]

done in 0.09 seconds, 97.03 sentences/sec


In [11]:
import json
print("\nResults for Nguyen2007\n\nMETHOD ONE\n")
print(json.dumps(one_n, indent=4))
print("\nMETHOD TWO")
print(json.dumps(two_n, indent=4))
print("\nResults for SemEval2010\n\nMETHOD ONE\n")
print(json.dumps(one_s, indent=4))
print("\nMETHOD TWO")
print(json.dumps(two_s, indent=4))

#Results with KeyBERT base model for both databases for comparison:

#                            NGUYEN2007                      SEMEVAL2010
#cosine_avg_precision:       0.03253588516746411             0.02880658436213992
#cosine_avg_recall:          0.03396966153906084             0.01910128664908381
#cosine_avg_f1_score:        0.030390087541456987            0.022781676955612812

#bert_avg_f1_score_cosine:   0.8658027230425084              0.862128734588623

#rouge1_avg_f1_score:        0.40740701819367736             0.39309364821299614
#rouge2_avg_f1_score:        0.09423142081493936             0.08073378608432674
#rougeL_avg_f1_score:        0.3275872620827588              0.3143067324860314


Results for Nguyen2007

METHOD ONE

{
    "cosine_avg_precision": 0.03684210526315789,
    "cosine_avg_recall": 0.03761042534728876,
    "cosine_avg_f1_score": 0.03416615141241346,
    "cosine_time": 0.0007801055908203125,
    "bert": {
        "bert_avg_precision_cosine": 0.8569737812306019,
        "bert_avg_recall_cosine": 0.8748538398996313,
        "bert_avg_f1_score_cosine": 0.8653773468859652,
        "bert_time": 158.07801127433777
    },
    "rouge": {
        "rouge1_avg_precision": 0.33540062782690067,
        "rouge1_avg_recall": 0.34200246353662117,
        "rouge1_avg_f1_score": 0.41336426054955244,
        "rouge2_avg_precision": 0.09535294375167103,
        "rouge2_avg_recall": 0.13428386830446204,
        "rouge2_avg_f1_score": 0.09569117293195825,
        "rougeL_avg_precision": 0.27782856583128573,
        "rougeL_avg_recall": 0.2901461466417966,
        "rougeL_avg_f1_score": 0.336136738173564,
        "rouge_time": 0.18189477920532227
    }
}

METHOD TWO
{
    "co